### Importing the required libraries


In [3]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json
#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim 
import requests
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans

from sklearn.metrics import silhouette_score
#!conda install -c conda-forge folium=0.5.0 --yes
import folium
# conda install -c anaconda beautiful-soup --yes
from bs4 import BeautifulSoup # package for parsing HTML and XML documents

import csv
print('Libraries imported.')


Libraries imported.


### New York Geographical Cordinates Data


In [4]:
!wget -q -O 'newyork_data.json' https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
print('Data downloaded!')

Data downloaded!


In [0]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']


In [6]:
#Converting the ata into pandas dataframe
neighborhoods = pd.DataFrame(columns=['Borough', 'Neighborhood', 'Latitude', 'Longitude'] )
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)


neighborhoods.head()



Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

### Raw material Data

In [7]:
from google.colab import drive
drive.mount('/content/drive')


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [0]:
markets = pd.read_csv("/content/drive/My Drive/Colab Notebooks/DOHMH_Farmers_Markets.csv")

In [9]:
markets.head()

Borough                       Market Name  \
0   Brooklyn     Woodhull Hospital Youthmarket   
1  Manhattan  Mount Sinai Hospital Greenmarket   
2      Bronx                    170 Farm Stand   
3  Manhattan       Greenmarket at Oculus Plaza   
4     Queens          Ditmars Park Youthmarket   

                                      Street Address   Latitude  Longitude  \
0                            Broadway & Flushing Ave  40.700726 -73.941932   
1                  E 99th St bet Madison & Park Aves  40.789169 -73.952743   
2                          E 170th St & Townsend Ave  40.839882 -73.916783   
3               Church & Fulton Sts, on Oculus Plaza  40.711535 -74.010464   
4  Steinway St bet Ditmars Blvd & 23rd Ave, at Di...  40.772854 -73.906061   

  Days of Operation Hours of Operations           Season Dates Accepts EBT  \
0         Wednesday     9 a.m. - 2 p.m.  07/10/2019-11/27/2019         Yes   
1         Wednesday     8 a.m. - 5 p.m.      06/12/19-11/27/19         Yes   
2         Wednesday    2:30 - 6:30 p.m.  07/10/2019-11/27/2019         Yes   
3           Tuesday     7 a.m. - 7 p.m.    07/09/2019-11/30/19         Yes   
4          Saturday     8 a.m. - 3 p.m.  07/13/2019-11/23/2019         Yes   

  Open Year-Round Stellar Cooking Demonstrations Food Activities for Kids  \
0              No                             No                       No   
1              No                             No                       No   
2              No                             No                      Yes   
3             Yes                             No                       No   
4              No                             No                       No   

            Location Point Unnamed: 13 Unnamed: 14  
0  (40.700726, -73.941932)         NaN         NaN  
1  (40.789169, -73.952743)         NaN         NaN  
2  (40.839882, -73.916783)         NaN         NaN  
3  (40.711535, -74.010464)         NaN         NaN  
4  (40.772854, -73.906061)         NaN         NaN

### Population Data



In [10]:

website_url = requests.get('https://en.wikipedia.org/wiki/Demographics_of_New_York_City').text
soup = BeautifulSoup(website_url,'lxml')
table = soup.find('table',{'class':'wikitable sortable'})
#print(soup.prettify())

headers = [header.text for header in table.find_all('th')]

table_rows = table.find_all('tr')        
rows = []
for row in table_rows:
   td = row.find_all('td')
   row = [row.text for row in td]
   rows.append(row)

with open('POPULATION.csv', 'w') as f:
   writer = csv.writer(f)
   writer.writerow(headers)
   writer.writerows(row for row in rows if row)

Pop_data=pd.read_csv('POPULATION.csv')
Pop_data.drop(Pop_data.columns[[7,8,9,10,11]], axis=1,inplace=True)
print('Data downloaded!')




Data downloaded!


In [11]:
Pop_data

New York City's five boroughsvte\n   Jurisdiction\n  \
0                                        The Bronx\n      \n  Bronx\n   
1                                         Brooklyn\n      \n  Kings\n   
2                                        Manhattan\n   \n  New York\n   
3                                           Queens\n    \n   Queens\n   
4                                    Staten Island\n  \n   Richmond\n   
5                                   City of New York        8,398,748   
6                                  State of New York       19,745,289   
7  Sources:[14] and see individual borough articl...              NaN   

  Population\n Gross Domestic Product\n Land area\n Density\n   Borough  \
0  1,432,132\n                 42.695\n    29,200\n   42.10\n  109.04\n   
1  2,582,830\n                 91.559\n    34,600\n   70.82\n  183.42\n   
2  1,628,701\n                600.244\n   360,900\n   22.83\n   59.13\n   
3  2,278,906\n                 93.310\n    39,600\n  108.53\n  281.09\n   
4    476,179\n                 14.514\n    30,300\n   58.37\n  151.18\n   
5      842.343                   97,700      302.64    783.83    28,188   
6    1,701.399                   85,700      47,214   122,284     416.4   
7          NaN                      NaN         NaN       NaN       NaN   

   squarekm  persons / sq. mi  persons /km2\n  
0       NaN               NaN             NaN  
1       NaN               NaN             NaN  
2       NaN               NaN             NaN  
3       NaN               NaN             NaN  
4       NaN               NaN             NaN  
5       NaN               NaN             NaN  
6       NaN               NaN             NaN  
7       NaN               NaN             NaN

In [0]:
Pop_data.columns=['Borough','County','Population','GDP','Landarea','Density','persons_sq_mi','one','two','three']


In [13]:

Pop_data.drop(['one','two','three'],axis=1,inplace=True)
Pop_data

Borough           County  \
0                                        The Bronx\n      \n  Bronx\n   
1                                         Brooklyn\n      \n  Kings\n   
2                                        Manhattan\n   \n  New York\n   
3                                           Queens\n    \n   Queens\n   
4                                    Staten Island\n  \n   Richmond\n   
5                                   City of New York        8,398,748   
6                                  State of New York       19,745,289   
7  Sources:[14] and see individual borough articl...              NaN   

    Population        GDP   Landarea   Density persons_sq_mi  
0  1,432,132\n   42.695\n   29,200\n   42.10\n      109.04\n  
1  2,582,830\n   91.559\n   34,600\n   70.82\n      183.42\n  
2  1,628,701\n  600.244\n  360,900\n   22.83\n       59.13\n  
3  2,278,906\n   93.310\n   39,600\n  108.53\n      281.09\n  
4    476,179\n   14.514\n   30,300\n   58.37\n      151.18\n  
5      842.343     97,700     302.64    783.83        28,188  
6    1,701.399     85,700     47,214   122,284         416.4  
7          NaN        NaN        NaN       NaN           NaN

In [14]:


Pop_data['Borough']=Pop_data['Borough'].replace(to_replace='\n', value='', regex=True)
Pop_data['County']=Pop_data['County'].replace(to_replace='\n', value='', regex=True)
Pop_data['Population']=Pop_data['Population'].replace(to_replace='\n', value='', regex=True)
Pop_data['Landarea']=Pop_data['Landarea'].replace(to_replace='\n', value='', regex=True)
Pop_data['Density']=Pop_data['Density'].replace(to_replace='\n', value='', regex=True)
Pop_data['persons_sq_mi']=Pop_data['persons_sq_mi'].replace(to_replace='\n', value='', regex=True)
Pop_data['GDP']=Pop_data['GDP'].replace(to_replace='\n', value='', regex=True)
Pop_data



Borough       County Population  \
0                                         The Bronx        Bronx  1,432,132   
1                                          Brooklyn        Kings  2,582,830   
2                                         Manhattan     New York  1,628,701   
3                                            Queens       Queens  2,278,906   
4                                     Staten Island     Richmond    476,179   
5                                  City of New York    8,398,748    842.343   
6                                 State of New York   19,745,289  1,701.399   
7  Sources:[14] and see individual borough articles          NaN        NaN   

       GDP Landarea  Density persons_sq_mi  
0   42.695   29,200    42.10        109.04  
1   91.559   34,600    70.82        183.42  
2  600.244  360,900    22.83         59.13  
3   93.310   39,600   108.53        281.09  
4   14.514   30,300    58.37        151.18  
5   97,700   302.64   783.83        28,188  
6   85,700   47,214  122,284         416.4  
7      NaN      NaN      NaN           NaN

In [15]:
Pop_data.drop(7, axis=0,inplace=True)
Pop_data

Borough       County Population      GDP Landarea  Density  \
0          The Bronx        Bronx  1,432,132   42.695   29,200    42.10   
1           Brooklyn        Kings  2,582,830   91.559   34,600    70.82   
2          Manhattan     New York  1,628,701  600.244  360,900    22.83   
3             Queens       Queens  2,278,906   93.310   39,600   108.53   
4      Staten Island     Richmond    476,179   14.514   30,300    58.37   
5   City of New York    8,398,748    842.343   97,700   302.64   783.83   
6  State of New York   19,745,289  1,701.399   85,700   47,214  122,284   

  persons_sq_mi  
0        109.04  
1        183.42  
2         59.13  
3        281.09  
4        151.18  
5        28,188  
6         416.4

### Cusine Data

The cusine information from the wikipedia page https://en.wikipedia.org/wiki/Cuisine_of_New_York_City was converted manually into a csv file and then used here. 

In [0]:
cusine=pd.read_csv("/content/drive/My Drive/Colab Notebooks/Cusine.csv")

In [17]:
cusine.head()

Unnamed: 0    Borough Neighbourhood                                Cuisine
0           0  The Bronx  Bedford Park  Mexican,Puerto Rican,Dominican,Korean
1           1  The Bronx       Belmont                       Italian,Albanian
2           2  The Bronx   City Island                        Italian,Seafood
3           3  The Bronx   Morris Park                       Italian,Albanian
4           4  The Bronx       Norwood                               Filipino

In [0]:
cusine.drop('Unnamed: 0',axis=1, inplace=True)

### Checking all the final data

In [19]:
# cusine data
cusine.head()

Borough Neighbourhood                                Cuisine
0  The Bronx  Bedford Park  Mexican,Puerto Rican,Dominican,Korean
1  The Bronx       Belmont                       Italian,Albanian
2  The Bronx   City Island                        Italian,Seafood
3  The Bronx   Morris Park                       Italian,Albanian
4  The Bronx       Norwood                               Filipino

In [20]:
# Population Data
Pop_data.head()

Borough       County Population      GDP Landarea Density  \
0      The Bronx        Bronx  1,432,132   42.695   29,200   42.10   
1       Brooklyn        Kings  2,582,830   91.559   34,600   70.82   
2      Manhattan     New York  1,628,701  600.244  360,900   22.83   
3         Queens       Queens  2,278,906   93.310   39,600  108.53   
4  Staten Island     Richmond    476,179   14.514   30,300   58.37   

  persons_sq_mi  
0        109.04  
1        183.42  
2         59.13  
3        281.09  
4        151.18

In [21]:
# Raw material market data

markets.head()

Borough                       Market Name  \
0   Brooklyn     Woodhull Hospital Youthmarket   
1  Manhattan  Mount Sinai Hospital Greenmarket   
2      Bronx                    170 Farm Stand   
3  Manhattan       Greenmarket at Oculus Plaza   
4     Queens          Ditmars Park Youthmarket   

                                      Street Address   Latitude  Longitude  \
0                            Broadway & Flushing Ave  40.700726 -73.941932   
1                  E 99th St bet Madison & Park Aves  40.789169 -73.952743   
2                          E 170th St & Townsend Ave  40.839882 -73.916783   
3               Church & Fulton Sts, on Oculus Plaza  40.711535 -74.010464   
4  Steinway St bet Ditmars Blvd & 23rd Ave, at Di...  40.772854 -73.906061   

  Days of Operation Hours of Operations           Season Dates Accepts EBT  \
0         Wednesday     9 a.m. - 2 p.m.  07/10/2019-11/27/2019         Yes   
1         Wednesday     8 a.m. - 5 p.m.      06/12/19-11/27/19         Yes   
2         Wednesday    2:30 - 6:30 p.m.  07/10/2019-11/27/2019         Yes   
3           Tuesday     7 a.m. - 7 p.m.    07/09/2019-11/30/19         Yes   
4          Saturday     8 a.m. - 3 p.m.  07/13/2019-11/23/2019         Yes   

  Open Year-Round Stellar Cooking Demonstrations Food Activities for Kids  \
0              No                             No                       No   
1              No                             No                       No   
2              No                             No                      Yes   
3             Yes                             No                       No   
4              No                             No                       No   

            Location Point Unnamed: 13 Unnamed: 14  
0  (40.700726, -73.941932)         NaN         NaN  
1  (40.789169, -73.952743)         NaN         NaN  
2  (40.839882, -73.916783)         NaN         NaN  
3  (40.711535, -74.010464)         NaN         NaN  
4  (40.772854, -73.906061)         NaN         NaN

In [22]:
# Geographical data
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

### Creating Clusters 


In [27]:

Clusters = neighborhoods.loc[(neighborhoods['Borough'] == 'Brooklyn')|(neighborhoods['Borough'] == 'Manhattan')]
Clusters = Clusters.reset_index(drop=True)
Clusters.head()

Borough Neighborhood   Latitude  Longitude
0  Manhattan  Marble Hill  40.876551 -73.910660
1   Brooklyn    Bay Ridge  40.625801 -74.030621
2   Brooklyn  Bensonhurst  40.611009 -73.995180
3   Brooklyn  Sunset Park  40.645103 -74.010316
4   Brooklyn   Greenpoint  40.730201 -73.954241

In [28]:
# Finding the cordinates of New York
address = 'New York City, NY'

geolocator = Nominatim(user_agent="Jupyter")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))


The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [30]:
# create map of Toronto using latitude and longitude values
map_BM = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(Clusters['Latitude'], Clusters['Longitude'], Clusters['Borough'], Clusters['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_BM)  
    
map_BM



In [0]:


CLIENT_ID = 'JFGH3PREVZK0JAEXJ4WANVT0C1XNAHHUC4NHYTBBA2OR2P0W' # your Foursquare ID
CLIENT_SECRET = 'L1JMFW35UOM0TZBH3BGXQOT1DGTZ5OL5EIGQPJ11BTAMVHUY' # your Foursquare Secret
VERSION = '20181218' # Foursquare API version


In [0]:
def getNearbyVenues(names, latitudes, longitudes, LIMIT=200, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)



In [33]:


BM_venues = getNearbyVenues(names=Clusters['Neighborhood'],
                                  latitudes=Clusters['Latitude'],
                                  longitudes=Clusters['Longitude'],
                                  LIMIT=200)

print('The "BM_venues" dataframe has {} venues and {} unique venue types.'.format(
      len(BM_venues['Venue Category']),
      len(BM_venues['Venue Category'].unique())))

BM_venues.head()



Marble Hill
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho

Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066    Bikram Yoga   
1  Marble Hill              40.876551               -73.91066       Arturo's   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066    Sam's Pizza   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.876844       -73.906204    Yoga Studio  
1       40.874412       -73.910271    Pizza Place  
2       40.880404       -73.908937          Diner  
3       40.879435       -73.905859    Pizza Place  
4       40.877531       -73.905582    Coffee Shop

In [0]:
# COnverting the data into a Pandas Dataframe
BM_Venues=pd.DataFrame(BM_venues)

In [35]:
BM_Venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Bath Beach                                    98                      98   
Battery Park City                            100                     100   
Bay Ridge                                    100                     100   
Bedford Stuyvesant                           100                     100   
Bensonhurst                                  100                     100   
Bergen Beach                                  10                      10   
Boerum Hill                                  100                     100   
Borough Park                                  54                      54   
Brighton Beach                                94                      94   
Broadway Junction                             51                      51   
Brooklyn Heights                             100                     100   
Brownsville                                   63                      63   
Bushwick                                     100                     100   
Canarsie                                      31                      31   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Central Harlem                               100                     100   
Chelsea                                      100                     100   
Chinatown                                    100                     100   
City Line                                     58                      58   
Civic Center                                 100                     100   
Clinton                                      100                     100   
Clinton Hill                                 100                     100   
Cobble Hill                                  100                     100   
Coney Island                                 100                     100   
Crown Heights                                100                     100   
Cypress Hills                                 42                      42   
Ditmas Park                                  100                     100   
Downtown                                     100                     100   
Dumbo                                        100                     100   
Dyker Heights                                 93                      93   
East Flatbush                                 32                      32   
East Harlem                                  100                     100   
East New York                                 25                      25   
East Village                                 100                     100   
East Williamsburg                            100                     100   
Erasmus                                       94                      94   
Financial District                           100                     100   
Flatbush                                     100                     100   
Flatiron                                     100                     100   
Flatlands                                     56                      56   
Fort Greene                                  100                     100   
Fort Hamilton                                100                     100   
Fulton Ferry                                 100                     100   
Georgetown                                    86                      86   
Gerritsen Beach                               61                      61   
Gowanus                                      100                     100   
Gramercy                                     100                     100   
Gravesend                                     53                      53   
Greenpoint                                   100                     100   
Greenwich Village                            100                     100   

In [36]:
# One hot encoding the whole data

BM_onehot = pd.get_dummies(BM_Venues[['Venue Category']], prefix="", prefix_sep="")

column_names = ['Neighborhood'] + list(BM_onehot.columns)

BM_onehot['Neighborhood'] = BM_Venues['Neighborhood'] 

BM_onehot = BM_onehot[column_names]

BM_onehot.head()



Neighborhood  ATM  Accessories Store  Adult Boutique  African Restaurant  \
0  Marble Hill    0                  0               0                   0   
1  Marble Hill    0                  0               0                   0   
2  Marble Hill    0                  0               0                   0   
3  Marble Hill    0                  0               0                   0   
4  Marble Hill    0                  0               0                   0   

   American Restaurant  Amphitheater  Animal Shelter  Antique Shop  Aquarium  \
0                    0             0               0             0         0   
1                    0             0               0             0         0   
2                    0             0               0             0         0   
3                    0             0               0             0         0   
4                    0             0               0             0         0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Bath House  Beach  Bed & Breakfast  \
0                 0                   0           0      0                0   
1                 0                   0           0      0                0   
2                 0                   0           0      0                0   
3                 0                   0           0      0                0   
4                 0                   0           0      0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  Bike Trail  \
0         0            0           0              0          0           0   
1         0            0           0              0          0           0   
2         0            0           0              0          0           0   
3         0            0           0              0          0           0   
4         0            0           0              0          0           0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0       0           0              0          0                 0         0   
1       0           0              0          0                 0         0   
2       0          

In [0]:
#Getting the list of restaurants in the area
Restaurant=[]
SearchTerm="Restaurant"
for i in BM_onehot.columns :
    if SearchTerm in i:
        Restaurant.append(i)

In [0]:
col_name = []
col_name = ['Neighborhood'] + Restaurant
BM_restaurant = BM_onehot[col_name]
BM_restaurant = BM_restaurant.iloc[:,1::]
BM_restaurant_grouped = BM_restaurant.groupby('Neighborhood').sum().reset_index()
BM_restaurant_grouped['Total'] = BM_restaurant_grouped .sum(axis=1)

In [39]:
# Creating clusters


BM_grouped_clustering = BM_restaurant_grouped.drop('Neighborhood', 1)

for n_cluster in range(2, 10):
    kmeans = KMeans(n_clusters=n_cluster).fit(BM_grouped_clustering)
    label = kmeans.labels_
    sil_coeff = silhouette_score(BM_grouped_clustering, label, metric='euclidean')
    print("For n_clusters={}, The Silhouette Coefficient is {}".format(n_cluster, sil_coeff))



For n_clusters=2, The Silhouette Coefficient is 0.36824964186120296
For n_clusters=3, The Silhouette Coefficient is 0.3139837434805402
For n_clusters=4, The Silhouette Coefficient is 0.22554063753522074
For n_clusters=5, The Silhouette Coefficient is 0.24433328518226058
For n_clusters=6, The Silhouette Coefficient is 0.2377177217962026
For n_clusters=7, The Silhouette Coefficient is 0.24294417952121217
For n_clusters=8, The Silhouette Coefficient is 0.17420081998967973
For n_clusters=9, The Silhouette Coefficient is 0.2268928843074058


In [40]:
#Creating a Kmeans with n=2 as it has the highest value of Silhouette Coefficient
kclusters = 2

BM_grouped_clustering = BM_restaurant_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(BM_grouped_clustering)

BM_results = pd.DataFrame(kmeans.cluster_centers_)
BM_results.columns = BM_grouped_clustering.columns
BM_results.index = ['cluster0','cluster1']
BM_results['Total Sum'] = BM_results.sum(axis = 1)
BM_results



African Restaurant  American Restaurant  Arepa Restaurant  \
cluster0            0.020833                 1.25          0.020833   
cluster1            0.112903                 2.00          0.096774   

          Argentinian Restaurant  Asian Restaurant  Australian Restaurant  \
cluster0                0.020833          0.145833           4.163336e-17   
cluster1                0.112903          0.661290           1.612903e-01   

          Austrian Restaurant  Brazilian Restaurant  Burmese Restaurant  \
cluster0             0.020833              0.020833       -1.734723e-18   
cluster1             0.096774              0.016129        1.612903e-02   

          Cajun / Creole Restaurant  Cambodian Restaurant  \
cluster0              -6.938894e-18              0.000000   
cluster1               6.451613e-02              0.048387   

          Cantonese Restaurant  Caribbean Restaurant  Caucasian Restaurant  \
cluster0          2.081668e-17              1.479167              0.041667   
cluster1          8.064516e-02              1.177419              0.048387   

          Chinese Restaurant  Colombian Restaurant  Comfort Food Restaurant  \
cluster0            1.020833         -1.734723e-18                 0.020833   
cluster1            1.419355          1.612903e-02                 0.096774   

          Cuban Restaurant  Czech Restaurant  Dim Sum Restaurant  \
cluster0          0.145833     -3.469447e-18       -6.938894e-18   
cluster1          0.290323      3.225806e-02        6.451613e-02   

          Dumpling Restaurant  Eastern European Restaurant  \
cluster0         2.775558e-17                     0.104167   
cluster1         1.129032e-01                     0.145161   

          Empanada Restaurant  English Restaurant  Ethiopian Restaurant  \
cluster0        -6.938894e-18       -3.469447e-18          4.163336e-17   
cluster1         6.451613e-02        3.225806e-02          1.612903e-01   

          Falafel Restaurant  Fast Food Restaurant  Filipino Restaurant  \
cluster0            0.062500              0.979167        -1.387779e-17   
cluster1            0.209677              0.354839         1.290323e-01   

          French Restaurant  German Restaurant  Greek Restaurant  \
cluster0           0.291667           0.020833            0.0625   
cluster1           1.080645           0.096774            0.5000   

          Halal Restaurant  Hawaiian Restaurant  Hotpot Restaurant  \
cluster0          0.020833         2.081668e-17           0.000000   
cluster1          0.080645         8.064516e-02           0.048387   

          Indian Restaurant  Israeli Restaurant  Italian Restaurant  \
cluster0           0.125000            0.000000            1.125000   
cluster1           0.854839            0.096774            2.951613   

          Japanese Curry Restaurant  Japanese Restaurant  Jewish Restaurant  \
cluster0                   0.041667             0.604167           0.000000   
cluster1                   0.032258             1.532258           0.048387   

          Kebab Restaurant  Korean Restaurant  Kosher Restaurant  \
cluster0     -3.469447e-18           0.020833           0.000000   
cluster1      3.225806e-02           0.500000           0.048387   

          Latin American Restaurant  Lebanese Restaurant  Malay Restaurant  \
cluster0                   0.416667         2.081668e-17      2.081668e-17   
cluster1                   0.822581         8.064516e-02      8.064516e-02   

          Mediterranean Restaurant  Mexican Restaurant  \
cluster0                  0.270833            0.750000   
cluster1                  0.580645            1.806452   

          Middle Eastern Restaurant  Molecular Gastronomy Restaurant  \
cluster0                   0.229167                    -3.469447e-18   
cluster1                   0.532258                     3.225806e-02   

          Moroccan Restaurant  New American Restaurant  \
cluster0        -6.938894e-18                 0.354167   
cluster1         6.45

In [41]:
#Creating a dataframe



BM_results_merged = pd.DataFrame(BM_restaurant_grouped['Neighborhood'])

BM_results_merged['Total'] = BM_restaurant_grouped['Total']
BM_results_merged = BM_results_merged.assign(Cluster_Labels = kmeans.labels_)

BM_results_merged.head()

Neighborhood  Total  Cluster_Labels
0          Bath Beach     32               1
1   Battery Park City     10               0
2           Bay Ridge     32               1
3  Bedford Stuyvesant     21               0
4         Bensonhurst     28               1

In [45]:
# Merging it with location data

BM_merged = Clusters

BM_merged = BM_merged.join(BM_results_merged.set_index('Neighborhood'), on='Neighborhood')

BM_merged.head(10)

Borough       Neighborhood   Latitude  Longitude  Total  Cluster_Labels
0  Manhattan        Marble Hill  40.876551 -73.910660     17               0
1   Brooklyn          Bay Ridge  40.625801 -74.030621     32               1
2   Brooklyn        Bensonhurst  40.611009 -73.995180     28               1
3   Brooklyn        Sunset Park  40.645103 -74.010316     39               1
4   Brooklyn         Greenpoint  40.730201 -73.954241     20               0
5   Brooklyn          Gravesend  40.595260 -73.973471      6               0
6   Brooklyn     Brighton Beach  40.576825 -73.965094     20               0
7   Brooklyn     Sheepshead Bay  40.586890 -73.943186     33               1
8   Brooklyn  Manhattan Terrace  40.614433 -73.957438     17               0
9   Brooklyn           Flatbush  40.636326 -73.958401     35               1

In [46]:
# Using Folium to visualize



# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(BM_merged['Latitude'], BM_merged['Longitude'], BM_merged['Neighborhood'], BM_merged['Cluster_Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters



In [47]:
## List of Neighborhooods 
BM_merged[BM_merged['Cluster_Labels'] == 1].reset_index(drop=True)


Borough               Neighborhood   Latitude  Longitude  Total  \
0    Brooklyn                  Bay Ridge  40.625801 -74.030621     32   
1    Brooklyn                Bensonhurst  40.611009 -73.995180     28   
2    Brooklyn                Sunset Park  40.645103 -74.010316     39   
3    Brooklyn             Sheepshead Bay  40.586890 -73.943186     33   
4    Brooklyn                   Flatbush  40.636326 -73.958401     35   
5    Brooklyn              Crown Heights  40.670829 -73.943291     22   
6    Brooklyn                 Kensington  40.642382 -73.980421     22   
7    Brooklyn           Prospect Heights  40.676822 -73.964859     29   
8    Brooklyn               Williamsburg  40.707144 -73.958115     26   
9    Brooklyn                   Bushwick  40.698116 -73.925258     25   
10   Brooklyn           Brooklyn Heights  40.695864 -73.993782     24   
11   Brooklyn                Cobble Hill  40.687920 -73.998561     24   
12   Brooklyn            Carroll Gardens  40.680540 -73.994654     21   
13   Brooklyn                Fort Greene  40.688527 -73.972906     29   
14   Brooklyn                 Park Slope  40.672321 -73.977050     24   
15   Brooklyn            Manhattan Beach  40.577914 -73.943537     22   
16   Brooklyn                 Bath Beach  40.599519 -73.998752     32   
17   Brooklyn              Dyker Heights  40.619219 -74.019314     22   
18   Brooklyn               Clinton Hill  40.693229 -73.967843     34   
19   Brooklyn                   Downtown  40.690844 -73.983463     23   
20   Brooklyn  Prospect Lefferts Gardens  40.658420 -73.954899     33   
21   Brooklyn        Prospect Park South  40.647009 -73.962613     33   
22   Brooklyn                 North Side  40.714823 -73.958809     25   
23   Brooklyn                 South Side  40.710861 -73.958001     26   
24   Brooklyn              Ocean Parkway  40.613060 -73.968367     24   
25   Brooklyn              Fort Hamilton  40.614768 -74.031979     27   
26  Manhattan                  Chinatown  40.715618 -73.994279     25   
27  Manhattan         Washington Heights  40.851903 -73.936900     33   
28  Manhattan                     Inwood  40.867684 -73.921210     32   
29  Manhattan           Hamilton Heights  40.823604 -73.949688     31   
30  Manhattan             Manhattanville  40.816934 -73.957385     33   
31  Manhattan             Central Harlem  40.815976 -73.943211     35   
32  Manhattan                East Harlem  40.792249 -73.944182     30   
33  Manhattan            Upper East Side  40.775639 -73.960508     25   
34  Manhattan                  Yorkville  40.775930 -73.947118     29   
35  Manhattan                 Lenox Hill  40.768113 -73.958860     29   
36  Manhattan           Roosevelt Island  40.762160 -73.949168     26   
37  Manhattan            Upper West Side  40.787658 -73.977059     33   
38  Manhattan                Murray Hill  40.748303 -73.978332     35   
39  Manhattan                    Chelsea  40.744035 -74.003116     21   
40  Manhattan          Greenwich Village  40.726933 -73.999914     31   
41  Manhattan               East Village  40.727847 -73.982226     29   
42  Manhattan            Lower East Side  40.717807 -73.980890     27   
43  Manhattan                    Tribeca  40.721522 -74.010683     23   
44  Manhattan               Little Italy  40.719324 -73.997305     25   
45  Manhattan                       Soho  40.722184 -74.000657     27   
46  Manhattan               West Village  40.734434 -74.006180     35   
47  Manhattan           Manhattan Valley  40.797307 -73.964286     31   
48  Manhattan        Morningside Heights  40.808000 -73.963896     32   
49  Manhattan                   Gramercy  40.737210 -73.981376     40   
50   Brooklyn                Ditmas Park  40.643675 -73.961013     32   
51  Manhattan              Carnegie Hill  40.782683 -73.953256     21   
52  Manhattan                       Noho  40.723259 -73.988434     35   
53  Manhattan               Civic Center  40.715229 -74.005415  

In [48]:
# Untapped Markets


BM_merged[BM_merged['Total'] == 0].reset_index(drop=True)




Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude, Total, Cluster_Labels]
Index: []

No Untapped markets in Brooklyn and Manhattan

### Creating Clusters 


In [49]:

Clusters1 = neighborhoods.loc[(neighborhoods['Borough'] == 'Bronx')|(neighborhoods['Borough'] == 'Queens')|(neighborhoods['Borough'] == 'Staten Island')]
Clusters1 = Clusters1.reset_index(drop=True)
Clusters1.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [50]:
# Finding the cordinates of New York
address = 'New York City, NY'

geolocator = Nominatim(user_agent="Jupyter")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))


The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [51]:
# create map of Toronto using latitude and longitude values
map_BM = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(Clusters1['Latitude'], Clusters1['Longitude'], Clusters1['Borough'], Clusters1['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_BM)  
    
map_BM



In [0]:


CLIENT_ID = 'JFGH3PREVZK0JAEXJ4WANVT0C1XNAHHUC4NHYTBBA2OR2P0W' # your Foursquare ID
CLIENT_SECRET = 'L1JMFW35UOM0TZBH3BGXQOT1DGTZ5OL5EIGQPJ11BTAMVHUY' # your Foursquare Secret
VERSION = '20181218' # Foursquare API version


In [0]:
def getNearbyVenues(names, latitudes, longitudes, LIMIT=200, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)



In [54]:


BM_venues1 = getNearbyVenues(names=Clusters1['Neighborhood'],
                                  latitudes=Clusters1['Latitude'],
                                  longitudes=Clusters1['Longitude'],
                                  LIMIT=200)

print('The "BM_venues" dataframe has {} venues and {} unique venue types.'.format(
      len(BM_venues1['Venue Category']),
      len(BM_venues1['Venue Category'].unique())))

BM_venues1.head()



Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cam

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0    Lollipops Gelato       40.894123       -73.845892          Dessert Shop  
1  Ripe Kitchen & Bar       40.898152       -73.838875  Caribbean Restaurant  
2     Ali's Roti Shop       40.894036       -73.856935  Caribbean Restaurant  
3    Carvel Ice Cream       40.890487       -73.848568        Ice Cream Shop  
4             Jimbo's       40.891740       -73.858226          Burger Joint

In [62]:
BM_Venues1

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                 Wakefield              40.894705              -73.847201   
1                 Wakefield              40.894705              -73.847201   
2                 Wakefield              40.894705              -73.847201   
3                 Wakefield              40.894705              -73.847201   
4                 Wakefield              40.894705              -73.847201   
5                 Wakefield              40.894705              -73.847201   
6                 Wakefield              40.894705              -73.847201   
7                 Wakefield              40.894705              -73.847201   
8                 Wakefield              40.894705              -73.847201   
9                 Wakefield              40.894705              -73.847201   
10                Wakefield              40.894705              -73.847201   
11                Wakefield              40.894705              -73.847201   
12                Wakefield              40.894705              -73.847201   
13                Wakefield              40.894705              -73.847201   
14                Wakefield              40.894705              -73.847201   
15                Wakefield              40.894705              -73.847201   
16                Wakefield              40.894705              -73.847201   
17                Wakefield              40.894705              -73.847201   
18                Wakefield              40.894705              -73.847201   
19                Wakefield              40.894705              -73.847201   
20                Wakefield              40.894705              -73.847201   
21                Wakefield              40.894705              -73.847201   
22                Wakefield              40.894705              -73.847201   
23                Wakefield              40.894705              -73.847201   
24                Wakefield              40.894705              -73.847201   
25                Wakefield              40.894705              -73.847201   
26                Wakefield              40.894705              -73.847201   
27                Wakefield              40.894705              -73.847201   
28                Wakefield              40.894705              -73.847201   
29                Wakefield              40.894705              -73.847201   
30                Wakefield              40.894705              -73.847201   
31                Wakefield              40.894705              -73.847201   
32                Wakefield              40.894705              -73.847201   
33                Wakefield              40.894705              -73.847201   
34                Wakefield              40.894705              -73.847201   
35                Wakefield              40.894705              -73.847201   
36                Wakefield              40.894705              -73.847201   
37                Wakefield              40.894705              -73.847201   
38                Wakefield              40.894705              -73.847201   
39                Wakefield              40.894705              -73.847201   
40                Wakefield              40.894705              -73.847201   
41                Wakefield              40.894705              -73.847201   
42                Wakefield              40.894705              -73.847201   
43                Wakefield              40.894705              -73.847201   
44                Wakefield              40.894705              -73.847201   
45                Wakefield              40.894705              -73.847201   
46                Wakefield              40.894705              -73.847201   
47                Wakefield              40.894705              -73.847201   
48               Co-op City              40.874294              -73.829939   
49               Co-op City              40.874294              -73.829939   
50               Co-op City          

In [0]:
# COnverting the data into a Pandas Dataframe
BM_Venues1=pd.DataFrame(BM_venues1)

In [57]:
BM_Venues1.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Allerton                                 69                      69     69   
Annadale                                 13                      13     13   
Arden Heights                            21                      21     21   
Arlington                                22                      22     22   
Arrochar                                 26                      26     26   
Arverne                                  32                      32     32   
Astoria                                 100                     100    100   
Astoria Heights                          72                      72     72   
Auburndale                              100                     100    100   
Bay Terrace                              92                      92     92   
Baychester                              100                     100    100   
Bayside                                 100                     100    100   
Bayswater                                 9                       9      9   
Bedford Park                             80                      80     80   
Beechhurst                               49                      49     49   
Bellaire                                 57                      57     57   
Belle Harbor                             24                      24     24   
Bellerose                                52                      52     52   
Belmont                                 100                     100    100   
Blissville                               74                      74     74   
Bloomfield                               25                      25     25   
Breezy Point                              4                       4      4   
Briarwood                                83                      83     83   
Broad Channel                            12                      12     12   
Bronxdale                               100                     100    100   
Brookville                               19                      19     19   
Bulls Head                               54                      54     54   
Butler Manor                              9                       9      9   
Cambria Heights                          33                      33     33   
Castle Hill                              40                      40     40   
Castleton Corners                        48                      48     48   
Charleston                               58                      58     58   
Chelsea                                  37                      37     37   
City Island                              41                      41     41   
Claremont Village                        18                      18     18   
Clason Point                              9                       9      9   
Clifton                                  61                      61     61   
Co-op City                               84                      84     84   
College Point                            73                      73     73   
Concord                                  41                      41     41   
Concourse                                70                      70     70   
Concourse Village                       100                     100    100   
Corona                                  100                     100    100   
Country Club                             72                      72     72   
Dongan Hills                             62                      62     62   
Douglaston                               62                      62     62   
East Elmhurst                            94                      94     94   
East Tremont                             71                      71     71   
Eastchester                              69                      69     69   
Edenwald                                 48 

In [59]:
# One hot encoding the whole data

BM_onehot1 = pd.get_dummies(BM_Venues1[['Venue Category']], prefix="", prefix_sep="")

column_names1 = ['Neighborhood'] + list(BM_onehot1.columns)

BM_onehot1['Neighborhood'] = BM_Venues1['Neighborhood'] 

BM_onehot1 = BM_onehot1[column_names1]

BM_onehot1.head()



Neighborhood  ATM  Accessories Store  Acupuncturist  Afghan Restaurant  \
0    Wakefield    0                  0              0                  0   
1    Wakefield    0                  0              0                  0   
2    Wakefield    0                  0              0                  0   
3    Wakefield    0                  0              0                  0   
4    Wakefield    0                  0              0                  0   

   African Restaurant  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0                    0             0       0                 0   
1                    0             0       0                 0   
2                    0             0       0                 0   
3                    0             0       0                 0   
4                    0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Australian Restaurant  Auto Dealership  Auto Garage  Automotive Shop  \
0                      0                0            0                0   
1                      0                0            0                0   
2                      0                0            0                0   
3                      0                0            0                0   
4                      0                0            0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0                 0           0      0          0                0         0   
1                 0           0      0          0                0         0   
2                 0           0      0          0                0         0   
3                 0           0      0          0                0         0   
4                 0           0      0          0                0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0            0           0              0                         0   
1            0           0              0                         0   
2            0           0              0                         0   
3            0           0              0                         0   
4            0           0              0                         0   

   

In [0]:
#Getting the list of restaurants in the area
Restaurant1=[]
SearchTerm="Restaurant"
for i in BM_onehot1.columns :
    if SearchTerm in i:
        Restaurant1.append(i)

In [0]:
col_name = []
col_name = ['Neighborhood'] + Restaurant1
BM_restaurant1 = BM_onehot1[col_name]
BM_restaurant1 = BM_restaurant1.iloc[:,1::]
BM_restaurant_grouped1 = BM_restaurant1.groupby('Neighborhood').sum().reset_index()
BM_restaurant_grouped1['Total'] = BM_restaurant_grouped1 .sum(axis=1)

In [0]:
# Creating clusters


BM_grouped_clustering1 = BM_restaurant_grouped1.drop('Neighborhood', 1)




In [69]:
#Creating a Kmeans with n=2 as it has the highest value of Silhouette Coefficient
kclusters = 2

BM_grouped_clustering1 = BM_restaurant_grouped1.drop('Neighborhood', 1)

# run k-means clustering
kmeans1 = KMeans(n_clusters=kclusters, random_state=0).fit(BM_grouped_clustering1)

BM_results1 = pd.DataFrame(kmeans.cluster_centers_)
BM_results1.columns = BM_grouped_clustering.columns
BM_results1.index = ['cluster0','cluster1']
BM_results1['Total Sum'] = BM_results1.sum(axis = 1)
BM_results1



African Restaurant  American Restaurant  Arepa Restaurant  \
cluster0            0.020833                 1.25          0.020833   
cluster1            0.112903                 2.00          0.096774   

          Argentinian Restaurant  Asian Restaurant  Australian Restaurant  \
cluster0                0.020833          0.145833           4.163336e-17   
cluster1                0.112903          0.661290           1.612903e-01   

          Austrian Restaurant  Brazilian Restaurant  Burmese Restaurant  \
cluster0             0.020833              0.020833       -1.734723e-18   
cluster1             0.096774              0.016129        1.612903e-02   

          Cajun / Creole Restaurant  Cambodian Restaurant  \
cluster0              -6.938894e-18              0.000000   
cluster1               6.451613e-02              0.048387   

          Cantonese Restaurant  Caribbean Restaurant  Caucasian Restaurant  \
cluster0          2.081668e-17              1.479167              0.041667   
cluster1          8.064516e-02              1.177419              0.048387   

          Chinese Restaurant  Colombian Restaurant  Comfort Food Restaurant  \
cluster0            1.020833         -1.734723e-18                 0.020833   
cluster1            1.419355          1.612903e-02                 0.096774   

          Cuban Restaurant  Czech Restaurant  Dim Sum Restaurant  \
cluster0          0.145833     -3.469447e-18       -6.938894e-18   
cluster1          0.290323      3.225806e-02        6.451613e-02   

          Dumpling Restaurant  Eastern European Restaurant  \
cluster0         2.775558e-17                     0.104167   
cluster1         1.129032e-01                     0.145161   

          Empanada Restaurant  English Restaurant  Ethiopian Restaurant  \
cluster0        -6.938894e-18       -3.469447e-18          4.163336e-17   
cluster1         6.451613e-02        3.225806e-02          1.612903e-01   

          Falafel Restaurant  Fast Food Restaurant  Filipino Restaurant  \
cluster0            0.062500              0.979167        -1.387779e-17   
cluster1            0.209677              0.354839         1.290323e-01   

          French Restaurant  German Restaurant  Greek Restaurant  \
cluster0           0.291667           0.020833            0.0625   
cluster1           1.080645           0.096774            0.5000   

          Halal Restaurant  Hawaiian Restaurant  Hotpot Restaurant  \
cluster0          0.020833         2.081668e-17           0.000000   
cluster1          0.080645         8.064516e-02           0.048387   

          Indian Restaurant  Israeli Restaurant  Italian Restaurant  \
cluster0           0.125000            0.000000            1.125000   
cluster1           0.854839            0.096774            2.951613   

          Japanese Curry Restaurant  Japanese Restaurant  Jewish Restaurant  \
cluster0                   0.041667             0.604167           0.000000   
cluster1                   0.032258             1.532258           0.048387   

          Kebab Restaurant  Korean Restaurant  Kosher Restaurant  \
cluster0     -3.469447e-18           0.020833           0.000000   
cluster1      3.225806e-02           0.500000           0.048387   

          Latin American Restaurant  Lebanese Restaurant  Malay Restaurant  \
cluster0                   0.416667         2.081668e-17      2.081668e-17   
cluster1                   0.822581         8.064516e-02      8.064516e-02   

          Mediterranean Restaurant  Mexican Restaurant  \
cluster0                  0.270833            0.750000   
cluster1                  0.580645            1.806452   

          Middle Eastern Restaurant  Molecular Gastronomy Restaurant  \
cluster0                   0.229167                    -3.469447e-18   
cluster1                   0.532258                     3.225806e-02   

          Moroccan Restaurant  New American Restaurant  \
cluster0        -6.938894e-18                 0.354167   
cluster1         6.45

In [73]:
#Creating a dataframe



BM_results_merged1 = pd.DataFrame(BM_restaurant_grouped1['Neighborhood'])

BM_results_merged1['Total'] = BM_restaurant_grouped1['Total']
BM_results_merged1 = BM_results_merged1.assign(Cluster_Labels1 = kmeans1.labels_)

BM_results_merged1.head()

Neighborhood  Total  Cluster_Labels1
0       Allerton     12                1
1       Annadale      2                1
2  Arden Heights      5                1
3      Arlington      3                1
4       Arrochar      5                1

In [79]:
# Merging it with location data

BM_merged1 = Clusters1

BM_merged1 = BM_merged1.join(BM_results_merged1.set_index('Neighborhood'), on='Neighborhood')

BM_merged1.head(10)

Borough    Neighborhood   Latitude  Longitude  Total  Cluster_Labels1
0   Bronx       Wakefield  40.894705 -73.847201      9                1
1   Bronx      Co-op City  40.874294 -73.829939     12                1
2   Bronx     Eastchester  40.887556 -73.827806     12                1
3   Bronx       Fieldston  40.895437 -73.905643      7                1
4   Bronx       Riverdale  40.890834 -73.912585      9                1
5   Bronx     Kingsbridge  40.881687 -73.902818     20                0
6   Bronx        Woodlawn  40.898273 -73.867315      8                1
7   Bronx         Norwood  40.877224 -73.879391     15                1
8   Bronx  Williamsbridge  40.881039 -73.857446     17                1
9   Bronx      Baychester  40.866858 -73.835798     13                1

In [80]:
## List of Neighborhooods 
BM_merged1[BM_merged1['Cluster_Labels1'] == 1].reset_index(drop=True)


Borough         Neighborhood   Latitude  Longitude  Total  \
0            Bronx            Wakefield  40.894705 -73.847201      9   
1            Bronx           Co-op City  40.874294 -73.829939     12   
2            Bronx          Eastchester  40.887556 -73.827806     12   
3            Bronx            Fieldston  40.895437 -73.905643      7   
4            Bronx            Riverdale  40.890834 -73.912585      9   
5            Bronx             Woodlawn  40.898273 -73.867315      8   
6            Bronx              Norwood  40.877224 -73.879391     15   
7            Bronx       Williamsbridge  40.881039 -73.857446     17   
8            Bronx           Baychester  40.866858 -73.835798     13   
9            Bronx       Pelham Parkway  40.857413 -73.854756      7   
10           Bronx          City Island  40.847247 -73.786488     15   
11           Bronx         Bedford Park  40.870185 -73.885512      9   
12           Bronx   University Heights  40.855727 -73.910416     12   
13           Bronx       Morris Heights  40.847898 -73.919672     10   
14           Bronx         East Tremont  40.842696 -73.887356      6   
15           Bronx           West Farms  40.839475 -73.877745      3   
16           Bronx         High  Bridge  40.836623 -73.926102      5   
17           Bronx              Melrose  40.819754 -73.909422     17   
18           Bronx           Mott Haven  40.806239 -73.916100     16   
19           Bronx          Port Morris  40.801664 -73.913221      8   
20           Bronx             Longwood  40.815099 -73.895788     16   
21           Bronx          Hunts Point  40.809730 -73.883315      5   
22           Bronx           Morrisania  40.823592 -73.901506     16   
23           Bronx            Soundview  40.821012 -73.865746      7   
24           Bronx         Clason Point  40.806551 -73.854144      1   
25           Bronx          Throgs Neck  40.815109 -73.816350      9   
26           Bronx         Country Club  40.844246 -73.824099     14   
27           Bronx   Westchester Square  40.840619 -73.842194     16   
28           Bronx             Van Nest  40.843608 -73.866299     13   
29           Bronx       Spuyten Duyvil  40.881395 -73.917190     10   
30           Bronx      North Riverdale  40.908543 -73.904531      7   
31           Bronx           Pelham Bay  40.850641 -73.832074     12   
32           Bronx        Schuylerville  40.826580 -73.826203     13   
33           Bronx       Edgewater Park  40.821986 -73.813885     13   
34           Bronx          Castle Hill  40.819014 -73.848027      5   
35           Bronx            Olinville  40.871371 -73.863324     15   
36           Bronx       Pelham Gardens  40.862966 -73.841612      6   
37           Bronx            Concourse  40.834284 -73.915589     17   
38           Bronx            Unionport  40.829774 -73.850535     18   
39           Bronx             Edenwald  40.884561 -73.848083     10   
40          Queens          Kew Gardens  40.705179 -73.829819     10   
41          Queens     Long Island City  40.750217 -73.939202     17   
42          Queens        East Elmhurst  40.764073 -73.867041     11   
43          Queens              Maspeth  40.725427 -73.896217     11   
44          Queens             Glendale  40.702762 -73.870742     11   
45          Queens            Woodhaven  40.689887 -73.858110     16   
46          Queens           Ozone Park  40.680708 -73.843203     12   
47          Queens     South Ozone Park  40.668550 -73.809865      9   
48          Queens        College Point  40.784903 -73.843045     12   
49          Queens           Whitestone  40.781291 -73.814202     13   
50          Queens            Glen Oaks  40.749441 -73.715481     13   
51          Queens            Bellerose  40.728573 -73.720128      6   
52          Queens    Kew Gardens Hills  40.722578 -73.820878     13   
53          Queens      Oakland Gardens  40.745619 -73.754950     15   
54          Queens       Queens Village  40.718893 

In [81]:
# Untapped Markets


BM_merged1[BM_merged1['Total'] == 0].reset_index(drop=True)




Borough  Neighborhood   Latitude  Longitude  Total  Cluster_Labels1
0  Staten Island     Todt Hill  40.597069 -74.111329      0                1
1  Staten Island    Port Ivory  40.639683 -74.174645      0                1
2  Staten Island  Butler Manor  40.506082 -74.229504      0                1
3  Staten Island     Rossville  40.549404 -74.215729      0                1
4  Staten Island    Bloomfield  40.605779 -74.187256      0                1

Based on the analysis, there is a scope for opening a restuarant in 4 neighborhoods in Staten Island ,in new York City' 